# Etude des notes pour le 2e trimestre

In [1]:
from IPython.display import Markdown as md
from IPython.display import display, HTML
import pandas as pd
import numpy as np
import ipywidgets as widgets
from pathlib import Path
from datetime import datetime
from recopytex import flat_df_students, pp_q_scores
from datetime import datetime
from pathlib import Path

import chart_studio.plotly as py
import plotly.graph_objects as go
import plotly.figure_factory as ff
import plotly.express as px

from plotly.offline import iplot, init_notebook_mode
init_notebook_mode()

In [2]:
score_files = list(Path("./").glob("**/*.csv"))
score_files

[PosixPath('230317_DS5.csv'),
 PosixPath('220922_DS1.csv'),
 PosixPath('230224_DS4.csv'),
 PosixPath('221201_DM1.csv'),
 PosixPath('230118_DS3.csv'),
 PosixPath('221214_DS2.csv')]

In [67]:
reject = ["221214_DS2.csv", "230317_DS5.csv"]
dfs = []
for file in score_files:
    if file.name not in reject:
        score_df = pd.read_csv(file, encoding="UTF8")
        flat = flat_df_students(score_df).dropna(subset=["Score"])
        pp_q = pp_q_scores(flat)
        dfs.append(pp_q)
df = pd.concat(dfs)

In [6]:
df = df.astype(dtype={
    "Nom": "str",
    "Trimestre": "int64",
    "Exercice": "str",
    "Question": "str",
    "Competence": "str",
    "Domaine": "str",
    "Commentaire": "str",
    "Est_nivele": "bool",
    "Bareme": "float64",
    "Eleve": "str",
    "Score": "float64",
    
})
df.Date = df.Date.apply(pd.to_datetime)

In [9]:
T2_df = df[df["Trimestre"] == 2]

## Fonctions

In [68]:
def build_pt(df, diff_col, eleve_col,  score_col, aggfunc):
    """ Fait une table pivot de df
    
    Préparation des données pour les clustering
    """
    pt = pd.pivot_table(df,
          index=[eleve_col],
          columns=[diff_col],
          values=[score_col],
          aggfunc=aggfunc,)
    pt.dropna(inplace=True)
    cols_names = pt.columns.get_level_values(-1)
    pt.columns = cols_names
    return pt.reset_index(), cols_names

In [69]:
def clustering(pt, cols_names, method, method_arg={}):
    """ Applique la méthode de clustering sur pt"""
    clu = method(**method_arg)
    clu.fit(pt[cols_names])
    return pd.Series(clu.labels_, index=pt.index), clu

In [89]:
def plot_polar_cluster(pt, clustername, clustering, fields):
    groups = pt.groupby([clustername]).agg({"Eleve":list})
    for i, cluster in enumerate(clustering.cluster_centers_):
        fig = go.Figure()
        fig.add_trace(go.Scatterpolar(
            r = cluster,
            theta = fields,
            name = i,
            fill="toself"
        ))
    

        for eleve in pt[pt[clustername]==i].iterrows():
           fig.add_trace(go.Scatterpolar(
                r = eleve[1][fields],
                theta = fields,
                name=eleve[1]["Eleve"],       
           ))
        fig.show()

## Classification des élèves


In [10]:
from sklearn.cluster import KMeans

In [11]:
T2_df = T2_df.assign(
    q_id = lambda x: x['Nom']+ x['Exercice'] + x['Question'] + x['Commentaire']
    )

## Sur les domaines

In [103]:
T2_pt_dom, domains = build_pt(T2_df, 
                             diff_col="Domaine", 
                             eleve_col="Eleve", 
                             score_col="Normalise", 
                             aggfunc=[np.mean])

In [104]:
T2_pt_dom["affinity_cluster"], affinity_cluster = clustering(T2_pt_dom, domains, AffinityPropagation)
T2_pt_dom["kmeans5_cluster"], kmeans5_cluster = clustering(T2_pt_dom, domains, KMeans, {'n_clusters':5, 'n_init':"auto"})
dom_clusters = {
    "affinity_cluster": affinity_cluster,
    "kmeans5_cluster": kmeans5_cluster,
}

In [105]:
plot_polar_cluster(T2_pt_dom, "kmeans5_cluster", dom_clusters["kmeans5_cluster"], domains)

### Sur les compétences

In [95]:
T2_pt_comp, domains = build_pt(T2_df, 
                             diff_col="Competence", 
                             eleve_col="Eleve", 
                             score_col="Normalise", 
                             aggfunc=[np.mean])

In [98]:
T2_pt_comp["affinity_cluster"], affinity_cluster = clustering(T2_pt_comp, domains, AffinityPropagation)
T2_pt_comp["kmeans5_cluster"], kmeans5_cluster = clustering(T2_pt_comp, domains, KMeans, {'n_clusters':5, 'n_init':"auto"})
comp_clusters = {
    "affinity_cluster": affinity_cluster,
    "kmeans5_cluster": kmeans5_cluster,
}

In [106]:
plot_polar_cluster(T2_pt_comp, "kmeans5_cluster", comp_clusters["kmeans5_cluster"], competences)

### Graphique en araignées pour les groupes

In [ ]:
inertia = []
for k in range(2, 20):
    clu = KMeans(n_clusters=k, n_init="auto")
    clu.fit(T2_pt_comp[competences])
    inertia.append(clu.inertia_)
print(inertia)

In [ ]:
inertia_df = pd.DataFrame({'index': range(2, 20), 'inertia':inertia})
px.line(inertia_df, x='index', y='inertia')